# Article Recommended System

In [1]:
import numpy as np
import pandas as pd
import nltk
import re
from sklearn.cluster import KMeans
from sklearn.feature_extraction.text import CountVectorizer 
from nltk.corpus import stopwords
from nltk.tokenize import word_tokenize
import gensim
import gensim.corpora as corpora
from gensim.utils import lemmatize

In [2]:
news = pd.read_csv(r"news_articles.csv")
news

Article_Id                                              Title  \
0              0  14 dead after bus falls into canal in Telangan...   
1              1  Pratibha Tiwari molested on busy road   Saath ...   
2              2  US  South Korea begin joint military drill ami...   
3              3  Illegal construction in Bengaluru  Will my hou...   
4              4  Punjab Gau Rakshak Dal chief held for assaulti...   
5              5  Phillipines drug war  1 800 drug-related death...   
6              6  Infosys shares likely to fall on Tuesday after...   
7              7  Dialogue crucial in finding permanent solution...   
8              8  School bus overturns in Jammu killing 1 and in...   
9              9  Rajasthan  Villagers rescue 50 kids after scho...   
10            10  Karnataka bus accident  8 schoolchildren dead ...   
11            11  Meghalaya accident  At least 30 killed and 8 i...   
12            12  Tamil Nadu  2 students dead  over 40 injured a...   
13            13  Uttarakhand  12 dead as bus falls into a gorge...   
14            14  42 missing in Mahad bridge collapse  Met says ...   
15            15  Mumbai-Goa bridge collapse  Two bodies recover...   
16            16  Mumbai-Goa bridge collapse  Death toll rises t...   
17            17  Mumbai-Goa bridge collapse  What we know so fa...   
18            18  Maharashtra  4 from Pune killed  1 injured in ...   
19            19  Uttar Pradesh  7 children dead after van hits ...   
20            20  Maharashtra  7-month-old baby survives Bhiwand...   
21            21  Madhya Pradesh  5 dead  10 injured in truck-je...   
22            22         26 killed after bus catches fire in Taiwan   
23            23  Jaipur  3 killed  5 injured as MLA s son alleg...   
24            24  Fire Breaks Out At Maharashtra Secretariat Com...   
25            25     18-Year-Old Killed in Mumbai Building Collapse   
26            26  Forensic Report Rules Out Sabotage As Cause Be...   
27            27   Star Trek  actor Anton Yelchin dead in fatal ...   
28            28  Multilingual actress Pranitha escapes road acc...   
29            29  Mumbai-Pune Expressway accident kills 17  inju...   
...          ...                                                ...   
4801        4801  India s rank goes up 12 notches in World Bank ...   
4802        4802  China Spent  147 billion To Halt Stock Market ...   
4803        4803  From Five-and-a-Half-Year Low to Three-Month H...   
4804        4804  Big B Invests in Fire Fighting Equipment Compa...   
4805        4805  Moody s Trims India s Growth Forecast to 7  Th...   
4806        4806      Sensex to Touch 32 200 by December 2015  Citi   
4807        4807  Can Sensex Gain from The Slump in Chinese Stoc...   
4808        4808  Sensex May Fall by Over 2 000 Points in Next 3...   
4809        4809  Gold Prices May See Free Fall on US Fed Rate Hike   
4810        4810     Gold Prices May Plunge to Rs 23 000 in a Month   
4811        4811  Rajesh Exports Buys 100  Stake in World s Larg...   
4812        4812  ASUS Zenfone 2 First Impression  A Well Config...   
4813        4813  Lenovo A7000 vs Asus Zenfone 2  ZE500CL  vs Mo...   
4814        4814  Asus Zenfone 2 Release Date  Features  Price  ...   
4815        4815  Top 10 Tips   Tricks for Gamers to Achieve Pin...   
4816        4816  Did You Know  Moto G  Moto E and Moto X have S...   
4817        4817  Six Essential Security Tips Every Whatsapp Use...   
4818        4818  Top 10 Smartphones and Gadgets Released at MWC...   
4819        4819  MWC 2015  Samsung Galaxy S6 Edge Wins Best New...   
4820        4820   Top Six 3D Printing Discoveries of February 2015   
4821        4821  Mobile World Congress 2015  1st Day Highlights...   
4822        4822  Samsung Galaxy S6 and Galaxy S6 Edge  6 Signif...   
4823        4823  HTC One M9 Plus Leaks Online  Expected Feature...   
4824        4824  Samsung Galaxy S6  S6 Edge Launched in India  ...   
4825        4825  iPhone 6 vs 

In [3]:
news = news[['Article_Id','Title','Content']].dropna() # to remove the nan rows
contents = news["Content"].tolist()
title = news['Title']
article_id = news['Article_Id']

In [4]:
from nltk.tokenize import word_tokenize
import re
STOPWORDS = stopwords.words('english')
# Here we are performing preprocessing. 
def clean_text(text):
    tokenized_text = word_tokenize(text.lower())
    cleaned_text = [t for t in tokenized_text if t not in STOPWORDS and re.match('[a-zA-Z\-][a-zA-Z\-]{2,}', t)]
    return cleaned_text
tokenized_data = []

# Here we are converting our content into token 
for i in contents :
    tokenized_data.append(clean_text(i))
tokenized_data

[['least',
  'people',
  'died',
  'others',
  'injured',
  'bus',
  'travelling',
  'hyderabad',
  'kakinada',
  'plunged',
  'canal',
  'bridge',
  'accident-prone',
  'stretch',
  'hyderabad-khammam',
  'highway',
  'telangana',
  'early',
  'monday',
  'morning',
  'injured',
  'admitted',
  'government',
  'general',
  'hospital',
  'treatment',
  'seven',
  'people',
  'died',
  'spot',
  'others',
  'succumbed',
  'injuries',
  'undergoing',
  'treatment',
  'hospital',
  'passengers',
  'belonged',
  'east',
  'west',
  'godavari',
  'districts',
  'andhra',
  'pradesh',
  'bus',
  'owned',
  'private',
  'operator',
  'yatra',
  'genie',
  'commenced',
  'journey',
  'hyderabad',
  'sunday',
  'khammam',
  'superintendent',
  'police',
  'shah',
  'nawaz',
  'khan',
  'quoted',
  'hindustan',
  'times',
  'saying',
  'accident',
  'happened',
  'around',
  'driver',
  'slammed',
  'brakes',
  'avoid',
  'collision',
  'another',
  'vehicle',
  'coming',
  'opposite',
  'direct

In [5]:
"""
Here are basically the performing bag of words method which tells count of word in given document.
"""

# Build a Dictionary - association word to numeric id
dictionary = corpora.Dictionary(tokenized_data)
# Transform the collection of texts to a numerical form
corpus = [dictionary.doc2bow(text) for text in tokenized_data]
corpus

[[(0, 2),
  (1, 1),
  (2, 1),
  (3, 1),
  (4, 1),
  (5, 1),
  (6, 1),
  (7, 1),
  (8, 1),
  (9, 1),
  (10, 1),
  (11, 3),
  (12, 4),
  (13, 4),
  (14, 1),
  (15, 1),
  (16, 1),
  (17, 1),
  (18, 1),
  (19, 1),
  (20, 2),
  (21, 1),
  (22, 1),
  (23, 1),
  (24, 2),
  (25, 1),
  (26, 1),
  (27, 1),
  (28, 1),
  (29, 1),
  (30, 1),
  (31, 1),
  (32, 1),
  (33, 1),
  (34, 1),
  (35, 1),
  (36, 1),
  (37, 1),
  (38, 1),
  (39, 1),
  (40, 1),
  (41, 2),
  (42, 2),
  (43, 1),
  (44, 1),
  (45, 1),
  (46, 2),
  (47, 1),
  (48, 1),
  (49, 1),
  (50, 2),
  (51, 1),
  (52, 1),
  (53, 1),
  (54, 1),
  (55, 1),
  (56, 1),
  (57, 1),
  (58, 1),
  (59, 1),
  (60, 1),
  (61, 1),
  (62, 1),
  (63, 1),
  (64, 1),
  (65, 1),
  (66, 2),
  (67, 1),
  (68, 1),
  (69, 1),
  (70, 2),
  (71, 1),
  (72, 2),
  (73, 1),
  (74, 1),
  (75, 1),
  (76, 1),
  (77, 2),
  (78, 1),
  (79, 1),
  (80, 1),
  (81, 1),
  (82, 1),
  (83, 1),
  (84, 1),
  (85, 1),
  (86, 1),
  (87, 1),
  (88, 1),
  (89, 1),
  (90, 1),
  (91, 1)

In [57]:
# """
# Here we are performing the topic modeling which tells the what is the probabilty of given word belong to one document.
# """
# from gensim.models import LdaModel
# lda = LdaModel(corpus=corpus, num_topics=4, id2word=dictionary, random_state=100,
#                 chunksize=1000, passes=50, minimum_probability = 0.0)

In [126]:
pd.to_pickle(lda,path ='./lda_out.txt')

In [127]:
lda= pd.read_pickle(path ='./lda_out.txt')

In [7]:
lda.print_topics(20)

[(0,
  '0.014*"india" + 0.011*"said" + 0.008*"year" + 0.007*"government" + 0.006*"crore" + 0.006*"percent" + 0.005*"prices" + 0.005*"also" + 0.004*"bank" + 0.004*"indian"'),
 (1,
  '0.012*"said" + 0.007*"police" + 0.006*"also" + 0.006*"people" + 0.005*"state" + 0.005*"minister" + 0.004*"india" + 0.004*"government" + 0.004*"isis" + 0.004*"two"'),
 (2,
  '0.012*"android" + 0.009*"note" + 0.009*"step" + 0.008*"device" + 0.008*"new" + 0.008*"smartphone" + 0.007*"galaxy" + 0.007*"also" + 0.007*"features" + 0.007*"camera"'),
 (3,
  '0.011*"film" + 0.006*"india" + 0.006*"movie" + 0.006*"also" + 0.005*"salman" + 0.005*"khan" + 0.005*"one" + 0.005*"first" + 0.004*"actor" + 0.003*"olympics"')]

In [8]:
myMatrix = list(lda[corpus])

In [9]:
X = np.array([[t[1] for t in lst] for lst in myMatrix])

In [10]:
X

array([[0.03662704, 0.95911956, 0.00208007, 0.00217337],
       [0.01519403, 0.48935527, 0.00249396, 0.49295676],
       [0.1234924 , 0.87243694, 0.00200312, 0.00206754],
       ...,
       [0.00158871, 0.00158081, 0.99524885, 0.00158161],
       [0.04669173, 0.01180797, 0.94019574, 0.00130454],
       [0.05119229, 0.00234099, 0.74485564, 0.20161113]], dtype=float32)

In [11]:
"""
Here we are using sil_coeff in order to get how much cluster we can have from the given data.
after we get sil_coeff we will choose cluster with bigger sil_coeff.
In the given case we have cluster 4 which have 0.844 values is the biggest so we will pass n_cluster=4 in the kmeans.
"""
from sklearn.metrics import silhouette_score
from sklearn.cluster import KMeans
for n_cluster in range(2, 11):
    kmeans = KMeans(n_clusters=n_cluster).fit(X)
    label = kmeans.labels_
    sil_coeff = silhouette_score(X, label, metric='euclidean')
    print("For n_clusters={}, The Silhouette Coefficient is {}".format(n_cluster, sil_coeff))

C:\Users\Student\Anaconda3\lib\site-packages\sklearn\metrics\pairwise.py:257: RuntimeWarning: invalid value encountered in sqrt
  return distances if squared else np.sqrt(distances, out=distances)


For n_clusters=2, The Silhouette Coefficient is 0.5297680497169495
For n_clusters=3, The Silhouette Coefficient is 0.716123104095459
For n_clusters=4, The Silhouette Coefficient is 0.8449310660362244
For n_clusters=5, The Silhouette Coefficient is 0.793984055519104
For n_clusters=6, The Silhouette Coefficient is 0.7781673073768616
For n_clusters=7, The Silhouette Coefficient is 0.7348779439926147
For n_clusters=8, The Silhouette Coefficient is 0.7208846211433411
For n_clusters=9, The Silhouette Coefficient is 0.6903650164604187
For n_clusters=10, The Silhouette Coefficient is 0.6763933300971985


In [12]:
#Now the clustering part so that we can have group of topic in order to recommended the article to user.
kmeans =  KMeans(n_clusters=4,random_state=101,max_iter=600)
model = kmeans.fit(X)
labels = model.labels_
a = labels

In [13]:
news["Clusters"]= pd.Series(a) # attach the labels with our dataframe

In [14]:
'''
In this cell we are creating the seprate cluster list for topic inorder to recommended them user to easily.
'''

zero_cluster =[]
one_cluster =[]
two_cluster =[]
third_cluster =[]

for i in range(1000):
    #print(news["Clusters"][:][i])
    if news["Clusters"][:][i]==0:
        #print("This is present in 0 Cluster")
        zero_cluster.append(i)
        #print(news.iloc[i])
    if news["Clusters"][:][i]==1:
        #print("This is present in 1 Cluster")
        one_cluster.append(i)
        #print(news.iloc[i])
    if news["Clusters"][:][i]==2:
        #print("This is present in 2 Cluster")
        two_cluster.append(i)
        #print(news.iloc[i])
    if news["Clusters"][:][i]==3:
        #print("This is present in 3 Cluster")
        third_cluster.append(i)
        #print(news.iloc[i])
              
    

In [108]:
mysample = []
t=4
z = 7-t
mysample.append(np.random.choice(zero_cluster))
mysample.append(np.random.choice(one_cluster))
mysample.append(np.random.choice(two_cluster))
mysample.append(np.random.choice(third_cluster))
for i in range(z):
    x = np.random.randint(1,4)
    if x==0:
        mysample.append(np.random.choice(zero_cluster))
        i=i+1
        if i==z:
            break
    if x==1:
        mysample.append(np.random.choice(one_cluster))
        if i==z:
            break
    if x==2:
        mysample.append(np.random.choice(two_cluster))
        i=i+1
        if i==z:
            break
    if x==3:
        mysample.append(np.random.choice(third_cluster))
        i=i+1
        if i==z:
            break
        

    
mysample

630

In [114]:
news.iloc[mysample[1]]

Article_Id                                                         797
Title                Ajith s wife Shalini does her bit for Chennai ...
Content              Kollywood have stood up for the people in Chen...
Clusters                                                             1
word_length                                                        843
Article_matrix                                                     nan
Average_word_time                                                168.6
actual_time                                                    30.3015
Name: 797, dtype: object

In [116]:
for i in mysample:
    print(news.iloc[i])

Article_Id                                                         154
Title                Nannaku Prematho 12 day box office collection ...
Content              Junior NTR s  Nannaku Prematho  has witnessed ...
Clusters                                                             0
word_length                                                       2003
Article_matrix                                                     nan
Average_word_time                                                400.6
actual_time                                                    29.9572
Name: 154, dtype: object
Article_Id                                                         797
Title                Ajith s wife Shalini does her bit for Chennai ...
Content              Kollywood have stood up for the people in Chen...
Clusters                                                             1
word_length                                                        843
Article_matrix                                      

In [15]:
news.head()

Article_Id                                              Title  \
0           0  14 dead after bus falls into canal in Telangan...   
1           1  Pratibha Tiwari molested on busy road   Saath ...   
2           2  US  South Korea begin joint military drill ami...   
3           3  Illegal construction in Bengaluru  Will my hou...   
4           4  Punjab Gau Rakshak Dal chief held for assaulti...   

                                             Content  Clusters  
0  At least 14 people died and 17 others were inj...         1  
1  TV actress Pratibha Tiwari  who is best known ...         0  
2  The United States and South Korea began a join...         1  
3  The relentless drive by Bengaluru s  Bangalore...         1  
4  Punjab Gau Raksha Dal chief Satish Kumar and h...         1

In [16]:
user_profile = {547:110,33:100,976:120,938:140}

In [17]:
user_profile

{547: 110, 33: 100, 976: 120, 938: 140}

In [18]:
avg_reading_speed = 5  #wordpersecond

In [19]:
X[537].reshape(4,1)

array([[0.05028277],
       [0.05154994],
       [0.05089683],
       [0.8472705 ]], dtype=float32)

In [20]:
z = user_profile.keys()

In [21]:
user_article  = [k for  k in  z]

In [22]:
user_article

[547, 33, 976, 938]

In [23]:
word_length =[]


for i in range(len(X)):
    word_length.append(len(news["Content"][i]))




In [24]:
news["word_length"]= pd.Series(word_length)

In [25]:
for i in range(len(X)):
    news["Article_matrix"]= pd.Series(X[i])

In [26]:
news.head()

Article_Id                                              Title  \
0           0  14 dead after bus falls into canal in Telangan...   
1           1  Pratibha Tiwari molested on busy road   Saath ...   
2           2  US  South Korea begin joint military drill ami...   
3           3  Illegal construction in Bengaluru  Will my hou...   
4           4  Punjab Gau Rakshak Dal chief held for assaulti...   

                                             Content  Clusters  word_length  \
0  At least 14 people died and 17 others were inj...         1         1363   
1  TV actress Pratibha Tiwari  who is best known ...         0         1222   
2  The United States and South Korea began a join...         1         1375   
3  The relentless drive by Bengaluru s  Bangalore...         1         2035   
4  Punjab Gau Raksha Dal chief Satish Kumar and h...         1         1475   

   Article_matrix  
0        0.051192  
1        0.002341  
2        0.744856  
3        0.201611  
4             NaN

In [27]:
user_profile.values()

dict_values([110, 100, 120, 140])

In [28]:
user_time = [k for k in user_profile.values()]

In [29]:
user_time

[110, 100, 120, 140]

In [30]:
word_avrg = []
for i in word_length:
    word_avrg.append(i/5)

In [31]:
news["Average_word_time"]= pd.Series(word_avrg) # word per second  5 is the average speed

In [32]:
news.head()

Article_Id                                              Title  \
0           0  14 dead after bus falls into canal in Telangan...   
1           1  Pratibha Tiwari molested on busy road   Saath ...   
2           2  US  South Korea begin joint military drill ami...   
3           3  Illegal construction in Bengaluru  Will my hou...   
4           4  Punjab Gau Rakshak Dal chief held for assaulti...   

                                             Content  Clusters  word_length  \
0  At least 14 people died and 17 others were inj...         1         1363   
1  TV actress Pratibha Tiwari  who is best known ...         0         1222   
2  The United States and South Korea began a join...         1         1375   
3  The relentless drive by Bengaluru s  Bangalore...         1         2035   
4  Punjab Gau Raksha Dal chief Satish Kumar and h...         1         1475   

   Article_matrix  Average_word_time  
0        0.051192              272.6  
1        0.002341              244.4  
2        0.744856              275.0  
3        0.201611              407.0  
4             NaN              295.0

In [33]:
user_time

[110, 100, 120, 140]

In [172]:
given_avg = []
for i in my_new_artcile:
    given_avg.append(news["Average_word_time"][i])

In [173]:
given_avg

[168.6, 352.4, 343.0]

In [174]:
my_ratio

[30.30152989915567, 29.841103818401397, 29.470200931100912]

In [176]:
time_ratio = []
for i in range(len(my_ratio)):
    time_ratio.append(my_ratio[i]/given_avg[i])

In [177]:
time_ratio

[0.1797243766260716, 0.08467963626107095, 0.08591895315189771]

In [178]:
import math

def sigmoid(x):
    return 1 / (1 + math.exp(-x))

In [179]:
sigmoid_time_ratio = []
for i in time_ratio:
    sigmoid_time_ratio.append(sigmoid(i))

In [180]:
sigmoid_time_ratio

[0.5448105408222109, 0.5211572679785247, 0.5214665342971064]

In [181]:
weight_matrix = np.array(sigmoid_time_ratio)


In [183]:
we = weight_matrix.reshape(3,1)
we.shape

(3, 1)

In [184]:
we[1][0]

0.5211572679785247

In [185]:
lda_user = []
for i in user_article:
    lda_user.append(X[i])

In [187]:
vector = []
for i in range(3):
    vector.append(lda_user[i]*we[i][0])
    

In [188]:
z_vector = np.array(vector)

In [189]:
final_vector_matrix = z_vector.sum(axis=0)

In [192]:
R = final_vector_matrix.reshape(-1, 1)
R1= R.reshape(1,4)


In [193]:
from sklearn.metrics.pairwise import cosine_similarity


In [194]:
d = cosine_similarity(R1,X)

In [51]:
# ut = []
# for i in range(len(d[0])):
#     if d[0][i]>0.7:
#         ut.append(d[0][i])

In [195]:
rt = np.array(d)
y = rt.flatten().argsort()[::-1]
zrt =[]
for i in range(len(y)):
    if y[i] not in user_article:
        zrt.append(y.tolist().pop(i))

In [196]:
zrt

[2130,
 4758,
 1906,
 3638,
 3547,
 1618,
 2635,
 1874,
 2909,
 1729,
 793,
 2065,
 3522,
 1872,
 1708,
 1759,
 579,
 807,
 3661,
 1881,
 1819,
 1546,
 3061,
 1319,
 3830,
 2013,
 860,
 1830,
 527,
 1676,
 2412,
 1764,
 1653,
 2948,
 2365,
 784,
 1887,
 1,
 2329,
 2106,
 3030,
 720,
 477,
 2495,
 1859,
 1630,
 201,
 1972,
 1957,
 2034,
 808,
 1566,
 2370,
 605,
 1663,
 809,
 2036,
 776,
 3027,
 1699,
 206,
 431,
 3266,
 2004,
 424,
 1965,
 1647,
 2829,
 2014,
 1602,
 2494,
 1880,
 1587,
 2020,
 575,
 2001,
 2628,
 1996,
 1706,
 1330,
 3328,
 796,
 1323,
 2184,
 2832,
 1962,
 291,
 1883,
 617,
 2128,
 3665,
 186,
 1995,
 1770,
 1713,
 513,
 2781,
 2173,
 828,
 1785,
 817,
 1999,
 1774,
 2990,
 1516,
 2137,
 855,
 868,
 1678,
 1832,
 1690,
 166,
 1495,
 1727,
 2172,
 790,
 551,
 1878,
 866,
 2359,
 848,
 1897,
 1912,
 2126,
 2513,
 1505,
 251,
 2118,
 596,
 3435,
 4653,
 208,
 2090,
 512,
 1620,
 3888,
 2149,
 1820,
 120,
 388,
 1837,
 1940,
 632,
 1715,
 825,
 1780,
 1487,
 2733,
 75,
 

In [197]:
s = rt.flatten().argsort()[::-1][:7]
s

array([2130, 4758, 1906, 3638, 3547, 1618, 2635], dtype=int64)

In [198]:
for i in s:
    print(news.iloc[i])
for i in range(3):
    rn = np.random.randint(1,4831,1)
    print( news.iloc[i])
   

Article_Id                                                        2130
Title                Mohanlal Offers to Return National Games Perfo...
Content              Actor Mohanlal has finally opened up about the...
Clusters                                                             0
word_length                                                       2509
Article_matrix                                                     nan
Average_word_time                                                501.8
actual_time                                                    20.2204
Name: 2130, dtype: object
Article_Id                                                        4758
Title                Woman Sues Coca Cola After Winning Contest Tha...
Content              A Chandigarh-based woman has filed a cheating ...
Clusters                                                             0
word_length                                                       1045
Article_matrix                                     

In [76]:
# Now the Genrative model part 
# for time 
time1 = np.random.normal(20,0.3,2000)
time2 = np.random.normal(30,0.3,2000)
time3 = np.random.normal(100,0.3,831)
total_time = np.append(time1,time2)
time = np.append(total_time,time3)
time

array([ 19.68348845,  20.7433093 ,  19.49224183, ...,  99.98105036,
        99.9619511 , 100.34688724])

In [82]:
news["actual_time"]= pd.Series(time)
news.head()

Article_Id                                              Title  \
0           0  14 dead after bus falls into canal in Telangan...   
1           1  Pratibha Tiwari molested on busy road   Saath ...   
2           2  US  South Korea begin joint military drill ami...   
3           3  Illegal construction in Bengaluru  Will my hou...   
4           4  Punjab Gau Rakshak Dal chief held for assaulti...   

                                             Content  Clusters  word_length  \
0  At least 14 people died and 17 others were inj...         1         1363   
1  TV actress Pratibha Tiwari  who is best known ...         0         1222   
2  The United States and South Korea began a join...         1         1375   
3  The relentless drive by Bengaluru s  Bangalore...         1         2035   
4  Punjab Gau Raksha Dal chief Satish Kumar and h...         1         1475   

   Article_matrix  Average_word_time  actual_time  
0        0.051192              272.6   100.056417  
1        0.002341              244.4    29.878203  
2        0.744856              275.0    20.394347  
3        0.201611              407.0    29.916921  
4             NaN              295.0   100.365276

In [83]:
news.drop(["Article_matrix"],axis=1)

Article_Id                                              Title  \
0              0  14 dead after bus falls into canal in Telangan...   
1              1  Pratibha Tiwari molested on busy road   Saath ...   
2              2  US  South Korea begin joint military drill ami...   
3              3  Illegal construction in Bengaluru  Will my hou...   
4              4  Punjab Gau Rakshak Dal chief held for assaulti...   
5              5  Phillipines drug war  1 800 drug-related death...   
6              6  Infosys shares likely to fall on Tuesday after...   
7              7  Dialogue crucial in finding permanent solution...   
8              8  School bus overturns in Jammu killing 1 and in...   
9              9  Rajasthan  Villagers rescue 50 kids after scho...   
10            10  Karnataka bus accident  8 schoolchildren dead ...   
11            11  Meghalaya accident  At least 30 killed and 8 i...   
12            12  Tamil Nadu  2 students dead  over 40 injured a...   
13            13  Uttarakhand  12 dead as bus falls into a gorge...   
14            14  42 missing in Mahad bridge collapse  Met says ...   
15            15  Mumbai-Goa bridge collapse  Two bodies recover...   
16            16  Mumbai-Goa bridge collapse  Death toll rises t...   
17            17  Mumbai-Goa bridge collapse  What we know so fa...   
18            18  Maharashtra  4 from Pune killed  1 injured in ...   
19            19  Uttar Pradesh  7 children dead after van hits ...   
20            20  Maharashtra  7-month-old baby survives Bhiwand...   
21            21  Madhya Pradesh  5 dead  10 injured in truck-je...   
22            22         26 killed after bus catches fire in Taiwan   
23            23  Jaipur  3 killed  5 injured as MLA s son alleg...   
24            24  Fire Breaks Out At Maharashtra Secretariat Com...   
25            25     18-Year-Old Killed in Mumbai Building Collapse   
26            26  Forensic Report Rules Out Sabotage As Cause Be...   
27            27   Star Trek  actor Anton Yelchin dead in fatal ...   
28            28  Multilingual actress Pranitha escapes road acc...   
29            29  Mumbai-Pune Expressway accident kills 17  inju...   
...          ...                                                ...   
4801        4801  India s rank goes up 12 notches in World Bank ...   
4802        4802  China Spent  147 billion To Halt Stock Market ...   
4803        4803  From Five-and-a-Half-Year Low to Three-Month H...   
4804        4804  Big B Invests in Fire Fighting Equipment Compa...   
4805        4805  Moody s Trims India s Growth Forecast to 7  Th...   
4806        4806      Sensex to Touch 32 200 by December 2015  Citi   
4807        4807  Can Sensex Gain from The Slump in Chinese Stoc...   
4808        4808  Sensex May Fall by Over 2 000 Points in Next 3...   
4809        4809  Gold Prices May See Free Fall on US Fed Rate Hike   
4810        4810     Gold Prices May Plunge to Rs 23 000 in a Month   
4811        4811  Rajesh Exports Buys 100  Stake in World s Larg...   
4812        4812  ASUS Zenfone 2 First Impression  A Well Config...   
4813        4813  Lenovo A7000 vs Asus Zenfone 2  ZE500CL  vs Mo...   
4814        4814  Asus Zenfone 2 Release Date  Features  Price  ...   
4815        4815  Top 10 Tips   Tricks for Gamers to Achieve Pin...   
4816        4816  Did You Know  Moto G  Moto E and Moto X have S...   
4817        4817  Six Essential Security Tips Every Whatsapp Use...   
4818        4818  Top 10 Smartphones and Gadgets Released at MWC...   
4819        4819  MWC 2015  Samsung Galaxy S6 Edge Wins Best New...   
4820        4820   Top Six 3D Printing Discoveries of February 2015   
4821        4821  Mobile World Congress 2015  1st Day Highlights...   
4822        4822  Samsung Galaxy S6 and Galaxy S6 Edge  6 Signif...   
4823        4823  HTC One M9 Plus Leaks Online  Expected Feature...   
4824        4824  Samsung Galaxy S6  S6 Edge Launched in India  ...   
4825        4825  iPhone 6 vs 

In [130]:
# articles which user have read.
user_read = np.random.poisson(3,1)[0]
        
my_new_artcile =np.random.choice(mysample,size=user_read)
        

In [131]:
my_new_artcile

array([797, 982, 956])

In [140]:
clicks = []
for i in mysample:
    if i in my_new_artcile:
        clicks.append("Yes")
    else:
        clicks.append("No")

In [141]:
clicks

['No', 'Yes', 'No', 'Yes', 'No', 'No', 'Yes']

In [154]:
user_table = pd.DataFrame(index = [mysample,clicks])

In [155]:
user_table

Empty DataFrame
Columns: []
Index: [(154, No), (797, Yes), (630, No), (982, Yes), (976, No), (963, No), (956, Yes)]

In [157]:
my_new_artcile

array([797, 982, 956])

In [158]:
news.head()

Article_Id                                              Title  \
0           0  14 dead after bus falls into canal in Telangan...   
1           1  Pratibha Tiwari molested on busy road   Saath ...   
2           2  US  South Korea begin joint military drill ami...   
3           3  Illegal construction in Bengaluru  Will my hou...   
4           4  Punjab Gau Rakshak Dal chief held for assaulti...   

                                             Content  Clusters  word_length  \
0  At least 14 people died and 17 others were inj...         1         1363   
1  TV actress Pratibha Tiwari  who is best known ...         0         1222   
2  The United States and South Korea began a join...         1         1375   
3  The relentless drive by Bengaluru s  Bangalore...         1         2035   
4  Punjab Gau Raksha Dal chief Satish Kumar and h...         1         1475   

   Article_matrix  Average_word_time  actual_time  
0        0.051192              272.6   100.056417  
1        0.002341              244.4    29.878203  
2        0.744856              275.0    20.394347  
3        0.201611              407.0    29.916921  
4             NaN              295.0   100.365276

In [167]:
my_ratio=[]
for i in my_new_artcile:
    my_ratio.append(news["actual_time"][i])

In [168]:
my_ratio

[30.30152989915567, 29.841103818401397, 29.470200931100912]